In [ ]:
# If you have a mac, please change from 'tk'
%matplotlib tk
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
import math
from datetime import datetime, timedelta

angle = 0
scale_val = math.sqrt(0.5)
currentEventIndex = 0
eventStartTime = datetime.now()
currentZoom = 1.0
maxDepth = 10
width, height = 800, 800

class Event:
    def __init__(self, targetAngle, targetScale, targetZoom, duration, isPause, changeScale, changeZoom):
        self.targetAngle = targetAngle
        self.targetScale = targetScale
        self.targetZoom = targetZoom
        self.duration = duration
        self.isPause = isPause
        self.changeScale = changeScale
        self.changeZoom = changeZoom

events = [
    Event(0, np.sqrt(0.5), 1, 1000, False, False, False),
    Event(45, np.sqrt(0.5), 1, 3000, False, False, False),
    Event(45, np.sqrt(0.5), 1, 1000, True, False, False),
    Event(60, np.sqrt(0.5), 1, 5000, False, False, False),
    Event(60, np.sqrt(0.5), 1, 1000, True, False, False),
    Event(90, np.sqrt(0.5), 1, 8000, False, False, False),
    Event(90, np.sqrt(0.5), 1, 5000, True, False, False),
    Event(60, np.sqrt(0.5), 1, 8000, False, False, False),
    Event(60, np.sqrt(0.5), 1, 1000, True, False, False),
    Event(60, 0.89, 0.5, 4000, False, True, True),
    Event(60, 0.89, 0.25, 5000, False, True, True),
]

def millis():
    return int((datetime.now() - eventStartTime).total_seconds() * 1000)

def lerp(start, stop, amt):
    return start + (stop - start) * amt

def rotate_vector(v, angle_degrees):
    angle_radians = math.radians(angle_degrees)
    rotation_matrix = np.array([[math.cos(angle_radians), -math.sin(angle_radians)],
                                [math.sin(angle_radians), math.cos(angle_radians)]])
    return np.dot(rotation_matrix, v)


cycleColors = [
    (0, 0, 255),   # Blue
    (128, 0, 128), # Purple
    (255, 192, 203), # Pink
    (255, 165, 0), # Orange
    (255, 255, 0), # Yellow
    (0, 128, 0),   # Green
    (64, 224, 208), # Turquoise
    (0, 0, 255),   # Blue
]

cycleDuration = 5000

def lerpColor(c1, c2, t):
    return tuple(a + (b - a) * t for a, b in zip(c1, c2))

def getColorForDepth(depth, maxDepth):
    baseCycleProgress = (millis() % cycleDuration) / cycleDuration

    depthOffset = depth / maxDepth
    cycleProgress = (baseCycleProgress - depthOffset) % 1.0

    colorIndex = int(cycleProgress * (len(cycleColors) - 1))
    lerpFactor = (cycleProgress * (len(cycleColors) - 1)) - colorIndex

    startColor = cycleColors[colorIndex]
    endColor = cycleColors[(colorIndex + 1) % len(cycleColors)]
    return lerpColor(startColor, endColor, lerpFactor)

def rec(ax, start, v, sc, a, count, currentDepth):
    if count <= 0:
        return

    end = start + v
    color = getColorForDepth(currentDepth, maxDepth)
    ax.plot([start[0], end[0]], [start[1], end[1]], color=np.array(color) / 255.0, linewidth=2)

    new_v = rotate_vector(v, a) * sc
    rec(ax, end, new_v, sc, a, count - 1, currentDepth + 1)

    new_v = rotate_vector(v, -a) * sc
    rec(ax, end, new_v, sc, -a, count - 1, currentDepth + 1)

def update(frame):
    global angle, scale_val, currentEventIndex, eventStartTime, currentZoom

    elapsedTime = millis()

    if frame == 0:
        eventStartTime = datetime.now()

    ax.clear()
    ax.set_xlim([0, width])
    ax.set_ylim([height, 0])
    ax.axis('off')

    if currentEventIndex < len(events):
        currentEvent = events[currentEventIndex]

        if currentEvent.changeScale:
            startScale = scale_val if currentEventIndex == 0 else events[currentEventIndex - 1].targetScale
            t = (elapsedTime - 0) / (currentEvent.duration - 0)
            scale_val = lerp(startScale, currentEvent.targetScale, t)

        if currentEvent.changeZoom:
            startZoom = currentZoom if currentEventIndex == 0 else events[currentEventIndex - 1].targetZoom
            t = (elapsedTime - 0) / (currentEvent.duration - 0)
            currentZoom = lerp(startZoom, currentEvent.targetZoom, t)

        if not currentEvent.isPause:
            startAngle = angle if currentEventIndex == 0 else math.radians(events[currentEventIndex - 1].targetAngle)
            t = (elapsedTime - 0) / (currentEvent.duration - 0)
            angle = lerp(startAngle, math.radians(currentEvent.targetAngle), t)

        if elapsedTime >= currentEvent.duration:
            angle = math.radians(currentEvent.targetAngle)
            scale_val = currentEvent.targetScale
            currentZoom = currentEvent.targetZoom

            currentEventIndex += 1
            eventStartTime = datetime.now()

    start = np.array([width / 2, height / 2])
    v = np.array([0, -height / 7 * currentZoom])
    rec(ax, start, v, scale_val, math.degrees(angle), maxDepth, 0)

    v_mirrored = np.array([0, height / 7 * currentZoom])
    rec(ax, start, v_mirrored, scale_val, math.degrees(angle), maxDepth, 0)
    
    

fig, ax = plt.subplots()

ani = FuncAnimation(fig, update, frames=np.arange(0, 600), repeat=False)

plt.show()